# Experiment 7

---

Stock Market Sentiment analysis, complete NLP pipeline.

## Import dependencies

In [127]:
import pandas as pd
import numpy as np
import re

import nltk
from nltk.stem import PorterStemmer
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords

from sklearn.feature_extraction.text import CountVectorizer
from sklearn.ensemble import RandomForestClassifier
from sklearn import svm
from sklearn.metrics import classification_report, accuracy_score, confusion_matrix
from sklearn.model_selection import train_test_split

from pprint import pprint

## Load data

In [128]:
data = pd.read_csv(r'C:\Users\kannu\OneDrive\Documents\github-repos\University\year-3\sem-6\cl-nlp\data\stock-news.csv', encoding ='ISO-8859-1')
data

Date  Label                                               Top1  \
0     2000-01-03      0  A 'hindrance to operations': extracts from the...   
1     2000-01-04      0                                          Scorecard   
2     2000-01-05      0                  Coventry caught on counter by Flo   
3     2000-01-06      1                      Pilgrim knows how to progress   
4     2000-01-07      1                               Hitches and Horlocks   
...          ...    ...                                                ...   
4096  2016-06-27      0  Barclays and RBS shares suspended from trading...   
4097  2016-06-28      1  2,500 Scientists To Australia: If You Want To ...   
4098  2016-06-29      1                   Explosion At Airport In Istanbul   
4099  2016-06-30      1  Jamaica proposes marijuana dispensers for tour...   
4100  2016-07-01      1  A 117-year-old woman in Mexico City finally re...   

                                                   Top2  \
0                                             Scorecard   
1                                   The best lake scene   
2                    United's rivals on the road to Rio   
3                                   Thatcher facing ban   
4                        Beckham off but United survive   
...                                                 ...   
4096  Pope says Church should ask forgiveness from g...   
4097  The personal details of 112,000 French police ...   
4098  Yemeni former president: Terrorism is the offs...   
4099  Stephen Hawking says pollution and 'stupidity'...   
4100   IMF chief backs Athens as permanent Olympic host   

                                                   Top3  \
0                       Hughes' instant hit buoys Blues   
1                         Leader: German sleaze inquiry   
2         Thatcher issues defence before trial by video   
3               McIlroy calls for Irish fighting spirit   
4                               Breast cancer screening   
...                                                 ...   
4096  Poland 'shocked' by xenophobic abuse of Poles ...   
4097  S&amp;P cuts United Kingdom sovereign credit r...   
4098  UK must accept freedom of movement to access E...   
4099  Boris Johnson says he will not run for Tory pa...   
4100  The president of France says if Brexit won, so...   

                                                   Top4  \
0              Jack gets his skates on at ice-cold Alex   
1                                         Cheerio, boyo   
2         Police help Smith lay down the law at Everton   
3                       Leicester bin stadium blueprint   
4                                           Alan Parker   
...                                                 ...   
4096  There will be no second referendum, cabinet ag...   
4097                Huge helium deposit found in Africa   
4098  Devastated: scientists too late to captive bre...   
4099  Six gay men in Ivory Coast were abused and for...   
4100  British Man Who Must Give Police 24 Hours' Not...   

                                                   Top5  \
0                Chaos as Maracana builds up for United   
1                              The main recommendations   
2           Tale of Trautmann bears two more retellings   
3                        United braced for Mexican wave   
4               Guardian readers: are you all whingers?   
...                                                 ...   
4096      Scotland welcome to join EU, Merkel ally says   
4097  CEO of the South African state broadcaster qui...   
4098  British Labor Party leader Jeremy Corbyn loses...   
4099  Switzerland denies citizenship to Muslim immig...   
4100  100+ Nobel laureates urge Greenpeace to stop o...   

                                                   Top6  \
0     Depleted Leicester prevail as Elliott spoils E...   
1                                Has Cubie killed fees?   
2                                   England on the rack   
3  

In [129]:
data.shape

(4101, 27)

In [130]:
data.columns

Index(['Date', 'Label', 'Top1', 'Top2', 'Top3', 'Top4', 'Top5', 'Top6', 'Top7',
       'Top8', 'Top9', 'Top10', 'Top11', 'Top12', 'Top13', 'Top14', 'Top15',
       'Top16', 'Top17', 'Top18', 'Top19', 'Top20', 'Top21', 'Top22', 'Top23',
       'Top24', 'Top25'],
      dtype='object')

In [131]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4101 entries, 0 to 4100
Data columns (total 27 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   Date    4101 non-null   object
 1   Label   4101 non-null   int64 
 2   Top1    4101 non-null   object
 3   Top2    4101 non-null   object
 4   Top3    4101 non-null   object
 5   Top4    4101 non-null   object
 6   Top5    4101 non-null   object
 7   Top6    4101 non-null   object
 8   Top7    4101 non-null   object
 9   Top8    4101 non-null   object
 10  Top9    4101 non-null   object
 11  Top10   4101 non-null   object
 12  Top11   4101 non-null   object
 13  Top12   4101 non-null   object
 14  Top13   4101 non-null   object
 15  Top14   4101 non-null   object
 16  Top15   4101 non-null   object
 17  Top16   4101 non-null   object
 18  Top17   4101 non-null   object
 19  Top18   4101 non-null   object
 20  Top19   4101 non-null   object
 21  Top20   4101 non-null   object
 22  Top21   4101 non-null   

In [132]:
data.isnull().sum()

Date     0
Label    0
Top1     0
Top2     0
Top3     0
Top4     0
Top5     0
Top6     0
Top7     0
Top8     0
Top9     0
Top10    0
Top11    0
Top12    0
Top13    0
Top14    0
Top15    0
Top16    0
Top17    0
Top18    0
Top19    0
Top20    0
Top21    0
Top22    0
Top23    1
Top24    3
Top25    3
dtype: int64

In [133]:
data.shape[0]

4101

## Extracting Data

Extracting the dates, labels, and statements from the dataset.

In [134]:
dates = data.iloc[ : , 0]
labels = data.iloc[ : , 1]

stmts = data.iloc[ : , 2:27]

In [135]:
dates.head()

0    2000-01-03
1    2000-01-04
2    2000-01-05
3    2000-01-06
4    2000-01-07
Name: Date, dtype: object

In [136]:
labels.head()

0    0
1    0
2    0
3    1
4    1
Name: Label, dtype: int64

In [137]:
stmts.head()

Top1  \
0  A 'hindrance to operations': extracts from the...   
1                                          Scorecard   
2                  Coventry caught on counter by Flo   
3                      Pilgrim knows how to progress   
4                               Hitches and Horlocks   

                                 Top2  \
0                           Scorecard   
1                 The best lake scene   
2  United's rivals on the road to Rio   
3                 Thatcher facing ban   
4      Beckham off but United survive   

                                            Top3  \
0                Hughes' instant hit buoys Blues   
1                  Leader: German sleaze inquiry   
2  Thatcher issues defence before trial by video   
3        McIlroy calls for Irish fighting spirit   
4                        Breast cancer screening   

                                            Top4  \
0       Jack gets his skates on at ice-cold Alex   
1                                  Cheerio, boyo   
2  Police help Smith lay down the law at Everton   
3                Leicester bin stadium blueprint   
4                                    Alan Parker   

                                          Top5  \
0       Chaos as Maracana builds up for United   
1                     The main recommendations   
2  Tale of Trautmann bears two more retellings   
3               United braced for Mexican wave   
4      Guardian readers: are you all whingers?   

                                                Top6  \
0  Depleted Leicester prevail as Elliott spoils E...   
1                             Has Cubie killed fees?   
2                                England on the rack   
3  Auntie back in fashion, even if the dress look...   
4                                   Hollywood Beyond   

                                              Top7  \
0                 Hungry Spurs sense rich pickings   
1                           Has Cubie killed fees?   
2  Pakistan retaliate with call for video of Walsh   
3                    Shoaib appeal goes to the top   
4                               Ashes and diamonds   

                                                Top8  \
0                  Gunners so wide of an easy target   
1                             Has Cubie killed fees?   
2               Cullinan continues his Cape monopoly   
3  Hussain hurt by 'shambles' but lays blame on e...   
4                   Whingers - a formidable minority   

                                                Top9  \
0      Derby raise a glass to Strupar's debut double   
1  Hopkins 'furious' at Foster's lack of Hannibal...   
2             McGrath puts India out of their misery   
3                      England's decade of disasters   
4                             Alan Parker - part two   

                                      Top10  ...  \
0  Southgate strikes, Leeds pay the penalty  ...   
1                    Has Cubie killed fees?  ...   
2            Blair Witch bandwagon rolls on  ...   
3      Revenge is sweet for jubilant Cronje  ...   
4                 Thuggery, Toxins and Ties  ...   

                                               Top16  \
0           Flintoff injury piles on woe for England   
1                               On the critical list   
2                        South Melbourne (Australia)   
3  Putin admits Yeltsin quit to give him a head s...   
4                             Most everywhere:  UDIs   

                                               Top17  \
0  Hunters threaten Jospin with new battle of the...   
1                          The timing of their lives   
2                                    Necaxa (Mexico)   
3         BBC worst hit as digital TV begins to bite   
4                       Most wanted:  Chloe lunettes   

                                            Top18  \
0             Kohl's successor drawn into scandal   
1                                     Dear doctor   
2                             Real Madrid (Spain)   
3 

Getting rid of all characters except for digits and characters:

In [138]:
stmts.replace("[^a-zA-Z0-9]"," ",regex=True, inplace=True)
stmts.head(2)

Top1                 Top2  \
0  A  hindrance to operations   extracts from the...            Scorecard   
1                                          Scorecard  The best lake scene   

                              Top3                                      Top4  \
0  Hughes  instant hit buoys Blues  Jack gets his skates on at ice cold Alex   
1    Leader  German sleaze inquiry                             Cheerio  boyo   

                                     Top5  \
0  Chaos as Maracana builds up for United   
1                The main recommendations   

                                                Top6  \
0  Depleted Leicester prevail as Elliott spoils E...   
1                             Has Cubie killed fees    

                               Top7                               Top8  \
0  Hungry Spurs sense rich pickings  Gunners so wide of an easy target   
1            Has Cubie killed fees              Has Cubie killed fees    

                                                Top9  \
0      Derby raise a glass to Strupar s debut double   
1  Hopkins  furious  at Foster s lack of Hannibal...   

                                      Top10  ...  \
0  Southgate strikes  Leeds pay the penalty  ...   
1                    Has Cubie killed fees   ...   

                                      Top16  \
0  Flintoff injury piles on woe for England   
1                      On the critical list   

                                               Top17  \
0  Hunters threaten Jospin with new battle of the...   
1                          The timing of their lives   

                                 Top18  \
0  Kohl s successor drawn into scandal   
1                          Dear doctor   

                                               Top19  \
0               The difference between men and women   
1  Irish court halts IRA man s extradition to Nor...   

                                               Top20  \
0                Sara Denver  nurse turned solicitor   
1  Burundi peace initiative fades after rebels re...   

                                            Top21  \
0  Diana s landmine crusade put Tories in a panic   
1            PE points the way forward to the ECB   

                                               Top22             Top23  \
0  Yeltsin s resignation caught opposition flat f...  Russian roulette   
1  Campaigners keep up pressure on Nazi war crime...    Jane Ratcliffe   

                                               Top24  \
0                                           Sold out   
1  Yet more things you wouldn t know without the ...   

                          Top25  
0            Recovering a title  
1  Millennium bug fails to bite  

[2 rows x 25 columns]

Renaming the column names for usability :)

In [139]:
stmts.columns = np.arange(0, stmts.shape[1])
stmts

0   \
0     A  hindrance to operations   extracts from the...   
1                                             Scorecard   
2                     Coventry caught on counter by Flo   
3                         Pilgrim knows how to progress   
4                                  Hitches and Horlocks   
...                                                 ...   
4096  Barclays and RBS shares suspended from trading...   
4097  2 500 Scientists To Australia  If You Want To ...   
4098                   Explosion At Airport In Istanbul   
4099  Jamaica proposes marijuana dispensers for tour...   
4100  A 117 year old woman in Mexico City finally re...   

                                                     1   \
0                                             Scorecard   
1                                   The best lake scene   
2                    United s rivals on the road to Rio   
3                                   Thatcher facing ban   
4                        Beckham off but United survive   
...                                                 ...   
4096  Pope says Church should ask forgiveness from g...   
4097  The personal details of 112 000 French police ...   
4098  Yemeni former president  Terrorism is the offs...   
4099  Stephen Hawking says pollution and  stupidity ...   
4100   IMF chief backs Athens as permanent Olympic host   

                                                     2   \
0                       Hughes  instant hit buoys Blues   
1                         Leader  German sleaze inquiry   
2         Thatcher issues defence before trial by video   
3               McIlroy calls for Irish fighting spirit   
4                               Breast cancer screening   
...                                                 ...   
4096  Poland  shocked  by xenophobic abuse of Poles ...   
4097  S amp P cuts United Kingdom sovereign credit r...   
4098  UK must accept freedom of movement to access E...   
4099  Boris Johnson says he will not run for Tory pa...   
4100  The president of France says if Brexit won  so...   

                                                     3   \
0              Jack gets his skates on at ice cold Alex   
1                                         Cheerio  boyo   
2         Police help Smith lay down the law at Everton   
3                       Leicester bin stadium blueprint   
4                                           Alan Parker   
...                                                 ...   
4096  There will be no second referendum  cabinet ag...   
4097                Huge helium deposit found in Africa   
4098  Devastated  scientists too late to captive bre...   
4099  Six gay men in Ivory Coast were abused and for...   
4100  British Man Who Must Give Police 24 Hours  Not...   

                                                     4   \
0                Chaos as Maracana builds up for United   
1                              The main recommendations   
2           Tale of Trautmann bears two more retellings   
3                        United braced for Mexican wave   
4               Guardian readers  are you all whingers    
...                                                 ...   
4096      Scotland welcome to join EU  Merkel ally says   
4097  CEO of the South African state broadcaster qui...   
4098  British Labor Party leader Jeremy Corbyn loses...   
4099  Switzerland denies citizenship to Muslim immig...   
4100  100  Nobel laureates urge Greenpeace to stop o...   

                                                     5   \
0     Depleted Leicester prevail as Elliott spoils E...   
1                                Has Cubie killed fees    
2                                   England on the rack   
3     Auntie back in fashion  even if the dress look...   
4                                      Hollywood Beyond   
...                                                 ...   
4096  Sterling dips below Friday s 31 year low amid ...   
4097  Brexit cost investors  2 trill

Merging all columns to form a list of sentences

In [141]:
sentences = []

for row in range(0, len(stmts.index)):
    
    # Merging all the columns, taking first 100 words in each row
    review = (' '.join(str(x) for x in stmts.iloc[row, : ])).split()
    review = review[ : 100]
    sentences.append(' '.join(x for x in review))
    
len(sentences)

4101

In [142]:
len(sentences[1])

560

In [143]:
pprint(sentences)

['A hindrance to operations extracts from the leaked reports Scorecard Hughes '
 'instant hit buoys Blues Jack gets his skates on at ice cold Alex Chaos as '
 'Maracana builds up for United Depleted Leicester prevail as Elliott spoils '
 'Everton s party Hungry Spurs sense rich pickings Gunners so wide of an easy '
 'target Derby raise a glass to Strupar s debut double Southgate strikes Leeds '
 'pay the penalty Hammers hand Robson a youthful lesson Saints party like it s '
 '1999 Wear wolves have turned into lambs Stump mike catches testy Gough s '
 'taunt Langer escapes to hit 167 Flintoff injury piles',
 'Scorecard The best lake scene Leader German sleaze inquiry Cheerio boyo The '
 'main recommendations Has Cubie killed fees Has Cubie killed fees Has Cubie '
 'killed fees Hopkins furious at Foster s lack of Hannibal appetite Has Cubie '
 'killed fees A tale of two tails I say what I like and I like what I say '
 'Elbows Eyes and Nipples Task force to assess risk of asteroid collisi

## Processing Sentences

Applying all the steps to clean the data.

In [144]:
PS = PorterStemmer()
WN = WordNetLemmatizer()

corpus = []

stopWords = set(stopwords.words('english'))

for i in range (len(sentences)):
  review = re.sub(r"http\S+", "", sentences[i])
#   review = re.sub('\n', ' ', review)
#   review = re.sub('[^a-zA-Z]', ' ', review)
  review = review.lower()
  review = review.split()
  review = [word for word in review if word not in set(stopwords.words('english'))]
  review = [PS.stem(word) for word in review]
  review = [WN.lemmatize(word) for word in review]
  review = ' '.join(review)
  corpus.append(review)

In [145]:
pprint(corpus)
len(corpus)

['hindranc oper extract leak report scorecard hugh instant hit buoy blue jack '
 'get skate ice cold alex chao maracana build unit deplet leicest prevail '
 'elliott spoil everton parti hungri spur sen rich pick gunner wide easi '
 'target derbi rais glass strupar debut doubl southgat strike leed pay penalti '
 'hammer hand robson youth lesson saint parti like 1999 wear wolv turn lamb '
 'stump mike catch testi gough taunt langer escap hit 167 flintoff injuri pile',
 'scorecard best lake scene leader german sleaz inquiri cheerio boyo main '
 'recommend cubi kill fee cubi kill fee cubi kill fee hopkin furiou foster '
 'lack hannib appetit cubi kill fee tale two tail say like like say elbow eye '
 'nippl task forc ass risk asteroid collis found last critic list time live '
 'dear doctor irish court halt ira man extradit northern ireland burundi peac '
 'initi fade rebel',
 'coventri caught counter flo unit rival road rio thatcher issu defenc trial '
 'video polic help smith lay law evert

4101

As we can see, our sentences have been preserved and processed.

## Vectorizing Sentences

Forming a simple bag-of-words model.

In [147]:
vectorizer = CountVectorizer(ngram_range=(2, 2))
corpusVector = vectorizer.fit_transform(corpus)
pprint(corpusVector)

<4101x226678 sparse matrix of type '<class 'numpy.int64'>'
	with 274361 stored elements in Compressed Sparse Row format>


## Splitting into Training and Testing

In [148]:
X_train, X_test, y_train, y_test = train_test_split(corpusVector, labels, test_size=0.33, shuffle=True, random_state=26)

In [149]:
X_train.shape, X_test.shape

((2747, 226678), (1354, 226678))

In [150]:
y_train.shape, y_test.shape

((2747,), (1354,))

67-33 split between training and testing.

## Random Forest Classification

In [151]:
randForClf = RandomForestClassifier(criterion='entropy')
randForClf.fit(X_train ,y_train)

RandomForestClassifier(criterion='entropy')

In [157]:
yPreds = randForClf.predict(X_test)
print(f'{classification_report(y_test, yPreds)} \n\nAccuracy for Random Forest Classifier: {accuracy_score(y_test, yPreds) * 100:.2f} %')

              precision    recall  f1-score   support

           0       0.14      0.00      0.00       639
           1       0.53      0.99      0.69       715

    accuracy                           0.52      1354
   macro avg       0.33      0.50      0.35      1354
weighted avg       0.35      0.52      0.36      1354
 

Accuracy for Random Forest Classifier: 52.44 %


In [153]:
conf_matrix = confusion_matrix(y_test, yPreds)
print(conf_matrix)

[[  1 638]
 [  6 709]]


## Support Vector Classification

In [154]:
model = svm.SVC()

model.fit(X_train, y_train)

yPredicted = model.predict(X_test)

In [158]:
print(f'{classification_report(y_test, yPredicted)} \n\nAccuracy for Support Vector Classifier: {accuracy_score(y_test, yPredicted) * 100:.2f} %')

              precision    recall  f1-score   support

           0       0.67      0.01      0.02       639
           1       0.53      0.99      0.69       715

    accuracy                           0.53      1354
   macro avg       0.60      0.50      0.36      1354
weighted avg       0.59      0.53      0.38      1354
 

Accuracy for Support Vector Classifier: 53.10 %


In [156]:
conf_matrix = confusion_matrix(y_test, yPredicted)
print(conf_matrix)

[[  8 631]
 [  4 711]]
